In [1]:
# !cp -rf /content/drive/MyDrive/ML\ Projects/Gemini-Pro/docs /content/

In [1]:
# !pip install langchain
# !pip install pypdf
# !pip install langchain_google_genai
# !pip install google-generativeai
# !pip install chromadb
# !pip install gradio
# !pip install faiss-cpu

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 KB 604.5 kB/s eta 0:00:00a 0:00:01
  Using cached tenacity-8.2.3-py3-none-any.whl (24 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 1.7 MB/s eta 0:00:0000:0100:01
  Using cached requests-2.31.0-py3-none-any.whl (62 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 2.0 MB/s eta 0:00:0000:0100:01
  Using cached langchain_core-0.1.10-py3-none-any.whl (216 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 1.1 MB/s eta 0:00:00eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 KB 594.8 kB/s eta 0:00:00 0:00:01
  Using cached PyYAML-6.0.1-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (705 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 524.5 kB/s eta 0:00:0000:0100:04
  Using cached async_timeout-4.0.3-py3-none-any.whl (5.7 kB)
  Using cached pydantic-2.5.3-py3-none-any.whl (381 kB)
  Using cached jsonpatch-1.33-py2.py3-none-any.whl (12 kB)
  Using cached aio

In [2]:
import os
from langchain.document_loaders import (
    PyPDFLoader,
    TextLoader,
    Docx2txtLoader
)

from langchain.text_splitter import CharacterTextSplitter
# from PyPDF2 import PdfReader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_google_genai import GoogleGenerativeAIEmbeddings
import google.generativeai as genai
from langchain.vectorstores import FAISS
from langchain_google_genai import ChatGoogleGenerativeAI
from langchain.chains.question_answering import load_qa_chain
from langchain.prompts import PromptTemplate
from dotenv import load_dotenv

/home/vasim/Khatir/Programming/ML Projects/gemini-pro with docs/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:

load_dotenv()

# genai.configure(api_key=userdata.get("GOOGLE_API_KEY"))

True

In [4]:
# document=[]
# for file in os.listdir("docs"):
#   if file.endswith(".pdf"):
#     pdf_path="./docs/"+file
#     loader=PyPDFLoader(pdf_path)
#     document.extend(loader.load())
#   elif file.endswith('.docx') or file.endswith('.doc'):
#     doc_path="./docs/"+file
#     loader=Docx2txtLoader(doc_path)
#     document.extend(loader.load())
#   elif file.endswith('.txt'):
#     text_path="./docs/"+file
#     loader=TextLoader(text_path)
#     document.extend(loader.load())

In [5]:
def extract_text(docs):
    documents = []
    files = os.listdir(docs)
    
    if len(files) == 0:
        return "Directory is empty"

    base_dir = docs.split("/")
    base_dir = "/".join(base_dir)
    
    print(files)
    print(base_dir)

    for file in files:
        if file.endswith(".pdf"):
            pdf_path=os.path.join(base_dir, file)
            loader=PyPDFLoader(pdf_path)
            documents.extend(loader.load())
        elif file.endswith('.docx') or file.endswith('.doc'):
            doc_path=os.path.join(base_dir, file)
            loader=Docx2txtLoader(doc_path)
            documents.extend(loader.load())
        elif file.endswith('.txt'):
            text_path=os.path.join(base_dir, file)
            loader=TextLoader(text_path)
            documents.extend(loader.load())
    return documents

In [6]:
doc_dir = "../docs"

In [7]:
documents = extract_text(doc_dir)

['profile.txt', 'llm-research.pdf']
../docs


In [8]:
documents[1]

Document(page_content='PREPRINT 1\nA Comprehensive Overview of\nLarge Language Models\nHumza Naveed1, Asad Ullah Khan1,∗, Shi Qiu2,∗, Muhammad Saqib3,4,∗,\nSaeed Anwar5,6, Muhammad Usman5,6, Naveed Akhtar7, Nick Barnes8, Ajmal Mian9\n1University of Engineering and Technology (UET), Lahore, Pakistan\n2The Chinese University of Hong Kong (CUHK), HKSAR, China\n3University of Technology Sydney (UTS), Sydney, Australia\n4Commonwealth Scientific and Industrial Research Organisation (CSIRO), Sydney, Australia\n5King Fahd University of Petroleum and Minerals (KFUPM), Dhahran, Saudi Arabia\n6SDAIA-KFUPM Joint Research Center for Artificial Intelligence (JRCAI), Dhahran, Saudi Arabia\n7The University of Melbourne (UoM), Melbourne, Australia\n8Australian National University (ANU), Canberra, Australia\n9The University of Western Australia (UWA), Perth, Australia\nAbstract —\nLarge Language Models (LLMs) have recently demonstrated\nremarkable capabilities in natural language processing tasks and\nb

In [9]:
len(documents)

47

In [10]:
# embeddings = GoogleGenerativeAIEmbeddings(model = "models/embedding-001")
# embeddings.embed_query("I am good")

In [11]:
def get_text_chunks(text):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=10000, chunk_overlap=1000)
    chunks = text_splitter.split_documents(text)
    return chunks

def get_vector_store(text_chunks, save=False):
    embeddings = GoogleGenerativeAIEmbeddings(model = "models/embedding-001")
    vector_store = FAISS.from_documents(text_chunks, embedding=embeddings)
    if not save:
        vector_store.save_local("faiss_index")
    return vector_store

In [12]:
documents = get_text_chunks(documents)

In [13]:
db = get_vector_store(documents)

In [14]:
def get_conversational_chain():

    prompt_template = """
    Answer the question as detailed as possible from the provided context, make sure to provide all the details, if the answer is not in
    provided context just say, "answer is not available in the context", don't provide the wrong answer\n\n
    Context:\n {context}?\n
    Question: \n{question}\n

    Answer:
    """

    model = ChatGoogleGenerativeAI(model="gemini-pro",temperature=0.3)

    prompt = PromptTemplate(template = prompt_template, input_variables = ["context", "question"])
    chain = load_qa_chain(llm=model, chain_type="stuff", prompt=prompt)

    return chain

In [15]:
llm = ChatGoogleGenerativeAI(model="gemini-pro",temperature=0.3)
llm.invoke("HII")

AIMessage(content='Hello! How can I assist you today?')

In [32]:
agent = get_conversational_chain()
def answer(question,agent=agent, db=db):
    docs = db.similarity_search(question)
    print(docs)
    response = agent(
        {"input_documents":docs, "question": question}
        ,return_only_outputs=True)
    return response

In [33]:
documents[5]

Document(page_content='PREPRINT 5\n2. Relative: To pass the information on the relative depen-\ndencies of different tokens appearing at different locations in\nthe sequence, a relative positional encoding is calculated by\nsome kind of learning. Two famous types of relative encodings\nare:\nAlibi: [65] In this approach, a scalar bias is subtracted from\nthe attention score calculated using two tokens which increases\nwith the distance between the positions of the tokens. This\nlearned approach effectively favors using recent tokens for\nattention.\nRoPE: Keys, queries, and values are all vectors in the LLMs.\nRoPE [66] involves the rotation of the query and key represen-\ntations at an angle proportional to their absolute positions of\nthe tokens in the input sequence. This step results in a relative\npositional encoding scheme which decays with the distance\nbetween the tokens.\nE. Activation Functions\nThe activation functions serve a crucial role in the curve-\nfitting abilities of

In [34]:
answer("what are the tokens")

[Document(page_content='HI, this is vasim an AI Engineer', metadata={'source': '../docs/profile.txt'}), Document(page_content='PREPRINT 23\nTABLE V: Architecture details of LLMs. Here, “PE” is the positional embedding, “nL” is the number of layers, “nH” is the\nnumber of attention heads, “HS” is the size of hidden states.\nModels TypeTraining\nObjectiveAttention Vocab Tokenizer Norm PE Activation Bias nL nH HS\nT5 (11B) Enc-Dec Span Corruption Standard 32k SentencePiece Pre-RMS Relative ReLU × 24 128 1024\nGPT3 (175B) Causal-Dec Next Token Dense+Sparse - - Layer Learned GeLU ✓ 96 96 12288\nmT5 (13B) Enc-Dec Span Corruption Standard 250k SentencePiece Pre-RMS Relative ReLU - - - -\nPanGu- α(200B) Causal-Dec Next Token Standard 40k BPE Layer - - - 64 128 16384\nCPM-2 (198B) Enc-Dec Span Corruption Standard 250k SentencePiece Pre-RMS Relative ReLU - 24 64 -\nCodex (12B) Causal-Dec Next Token Standard - BPE+ Pre-Layer Learned GeLU - 96 96 12288\nERNIE 3.0 (10B) Causal-Dec Next Token Standa

{'output_text': '    answer is not available in the context'}

In [20]:
# Gradio App
import gradio as gr

title = ""
description = f"Chat with any docs"

def answer_query(message, history):
    docs = db.similarity_search(message)
    message = agent(
        {"input_documents":docs, "question": message}
        ,return_only_outputs=True)
    return message['output_text']


demo = gr.ChatInterface(
    answer_query,
    title= title,
    description=description,
    examples=[
        ["What is a Large Language Model?"],
        ["What's 9+2-1?"],
        ["Write Python code to print the Fibonacci sequence"]
    ]
)

if __name__ == "__main__":
    demo.queue().launch()



Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.
